In [1]:
from modules.data_class import DataState
from modules.tools import data_node
from modules.nodes import chatbot_with_tools, human_node, maybe_exit_human_node, maybe_route_to_tools

from langgraph.graph import StateGraph, START, END
from langgraph.checkpoint.memory import MemorySaver

from IPython.display import Image, display
from pprint import pprint
from typing import Literal

from langgraph.prebuilt import ToolNode

from collections.abc import Iterable
from IPython.display import display, clear_output
import sys

In [2]:
graph_builder = StateGraph(DataState)
memory = MemorySaver()

# Nodes
graph_builder.add_node("chatbot_healthassistant", chatbot_with_tools)
graph_builder.add_node("patient", human_node)
graph_builder.add_node("documenting", data_node)

# Chatbot -> {ordering, tools, human, END}
graph_builder.add_conditional_edges("chatbot_healthassistant", maybe_route_to_tools)
# Human -> {chatbot, END}
graph_builder.add_conditional_edges("patient", maybe_exit_human_node)
# TestCase_Paintrek
# Tools (both kinds) always route back to chat afterwards.
graph_builder.add_edge("documenting", "chatbot_healthassistant")

graph_builder.add_edge(START, "chatbot_healthassistant")
graph_with_order_tools = graph_builder.compile(checkpointer=memory)

# Image(graph_with_order_tools.get_graph().draw_mermaid_png())

In [3]:
# This is for the checkpointer to have a thread id to remember for each user, and I don't know if letter mix with number will work here 
# The default recursion limit for traversing nodes is 25 - setting it higher means you can try a more complex order with multiple steps and round-trips.
config = {"configurable": {"thread_id": "1"}, "recursion_limit": 1000}

# Uncomment this line to execute the graph:
# Clear output before running new states
clear_output(wait=True)

# Ensure messages print immediately
print("Executing the chatbot graph...", flush=True)
state = graph_with_order_tools.invoke({"messages": []}, config)
# display(state)  # Ensures state is shown in Jupyter
# sys.stdout.flush()

# pprint(state)

Executing the chatbot graph...
Model: Welcome to the Paintrek world. I am a health assistant, an interactive clinical recording system. I will ask you questions about your pain and related symptoms and record your responses.  I will then store this information securely. At any time, you can type `q` to quit.
User: Let's start
Model: Great! Let’s begin by gathering some basic information. Could you please provide your full name, date of birth, and contact number? This will help us proceed with the medical record setup.
User: My name is Frank my DOB is 19860214, my contact number is 123456
Model: Thank you for providing your information, Frank. Could you please confirm your full date of birth and provide any additional contact details such as an email address or another phone number? Also, could you tell me about your emergency contacts if applicable?
If you're ready to proceed with the rest of the intake process now, let me know!
User: my date of birth is Feb 14 1986, emergency contact 

In [4]:
state["data"]

{'ID': {'name': '',
  'DOB': datetime.date(1900, 1, 1),
  'gender': '',
  'contact': '',
  'emergency_contact': ''},
 'symptom': {'main_symptom': '', 'symptom_length': ''},
 'pain': {'pain_location': '',
  'pain_side': '',
  'pain_intensity': 0,
  'pain_description': '',
  'start_time': datetime.date(1900, 1, 1),
  'radiation': False,
  'triggers': '',
  'symptom': ''},
 'medical_hist': {'medical_condition': '',
  'first_time': datetime.date(1900, 1, 1),
  'surgery_history': '',
  'medication': '',
  'allergy': ''},
 'family_hist': {'family_history': ''},
 'social_hist': {'occupation': '',
  'smoke': False,
  'alcohol': False,
  'drug': False,
  'support_system': '',
  'living_condition': ''},
 'review_system': {'weight_change': '',
  'fever': False,
  'chill': False,
  'night_sweats': False,
  'sleep': '',
  'gastrointestinal': '',
  'urinary': ''},
 'pain_manage': {'pain_medication': '',
  'specialist': False,
  'other_therapy': '',
  'effectiveness': False},
 'functional': {'life_qu